```
!cat \
filtered_106A_Female_Mix_GATCAG_L004_R1.fastq \
filtered_108A_Female_Mix_GGCTAC_L004_R1.fastq \
filtered_106A_Male_Mix_TAGCTT_L004_R1.fastq \
filtered_108A_Male_Mix_AGTCAA_L004_R1.fastq >> /Users/sr320/data-genomic/tentacle/OlyOv6/OlyOv6_combined_R1.fastq
!cat \
filtered_106A_Female_Mix_GATCAG_L004_R2.fastq \
filtered_108A_Female_Mix_GGCTAC_L004_R2.fastq \
filtered_106A_Male_Mix_TAGCTT_L004_R2.fastq \
filtered_108A_Male_Mix_AGTCAA_L004_R2.fastq >> /Users/sr320/data-genomic/tentacle/OlyOv6/OlyOv6_combined_R2.fastq
```

Trimming details @
<https://github.com/sr320/course-btea/blob/master/day-1/01-OlympiaOyster-transcriptome.ipynb>

# Assembly

```
#!/bin/sh

KMER=2

LD_LIBRARY_PATH=/share/bioinformatics/gcc/lib64:/share/bioinformatics/gcc/lib

TRIN=/data/ggoetz/trinityrnaseq-2.0.6
SAMTOOLS=/share/bioinformatics/samtools/bin
BOWTIE=/share/bioinformatics/bowtie

PATH=${SAMTOOLS}:${BOWTIE}:${PATH}

${TRIN}/Trinity \
	--seqType fq \
	--max_memory 400G \
	--left OlyOv6_combined_R1_val_1.fq \
	--right OlyOv6_combined_R2_val_2.fq \
	--CPU 8 \
	--bflyCalculateCPU \
	--bflyHeapSpaceMax 16G \
	--bflyHeapSpaceInit 8G \
	--normalize_reads \
	--min_kmer_cov ${KMER} \
	--output trinity_All.kmer${KMER} \
	> trinity_output.All.kmer${KMER}.log
```

In [1]:
!head /Users/sr320/data-genomic/tentacle/trinity.kmer2.fa

>TR1|c0_g1_i1 len=320 path=[639:0-301 640:302-319] [-1, 639, 640, -2]
GACGAAAAACAAACACATAATCAATCAATCAATCAATCAATCAAATAACAGAGATTCAAT
CCATAGTAACAGTATACCTTACAGCGATATAACAGTCTGGTTATTCTATAAAATCTATAT
CTACATGTATTATTAACACACATTACTTATTATATAATGTTCTGGTTGCTTGAATTATGG
AAGTATAAAAACAATGTATAACCGGGACCATTATTTATACAGAGAAAAACTAGCAAAGTG
TTTGGTTTTAAAACTCGAATTGACTGACATTGACAGTGGCATATTTATAATTTTGTAGGA
TGTTAATCAACACATAACAT
>TR1|c0_g2_i1 len=323 path=[637:0-301 638:302-322] [-1, 637, 638, -2]
GACGAAAAACAAACACATAATCAATCAATCAATCAATCAATCAAATAACAGAGATTCAAT
CCATAGTAACAGTATACCTTACAGCGATATAACAGTCTGGTTATTCTATAAAATCTATAT


In [4]:
!fgrep ">" /Volumes/Monarch/quarter-shell/OlyO_v6_transcriptome.fa | head -50


>TR1|c0_g1_i1 len=320 path=[639:0-301 640:302-319] [-1, 639, 640, -2]
>TR1|c0_g2_i1 len=323 path=[637:0-301 638:302-322] [-1, 637, 638, -2]
>TR2|c0_g1_i1 len=359 path=[834:0-181 838:182-235 837:236-358] [-1, 834, 838, 837, -2]
>TR3|c0_g1_i1 len=256 path=[234:0-255] [-1, 234, -2]
>TR4|c0_g1_i1 len=330 path=[706:0-106 707:107-130 709:131-223 705:224-329] [-1, 706, 707, 709, 705, -2]
>TR5|c0_g1_i1 len=226 path=[407:0-225] [-1, 407, -2]
>TR6|c0_g1_i1 len=400 path=[804:0-194 805:195-218 806:219-399] [-1, 804, 805, 806, -2]
>TR7|c0_g1_i1 len=311 path=[577:0-310] [-1, 577, -2]
>TR8|c0_g1_i1 len=378 path=[760:0-264 761:265-288 762:289-377] [-1, 760, 761, 762, -2]
>TR9|c0_g1_i1 len=256 path=[755:0-51 765:52-64 763:65-75 761:76-122 759:123-179 742:180-203 743:204-255] [-1, 755, 765, 763, 761, 759, 742, 743, -2]
>TR10|c0_g1_i1 len=240 path=[985:0-191 986:192-194 987:195-239] [-1, 985, 986, 987, -2]
>TR10|c0_g2_i1 len=453 path=[982:0-146 983:147-170 988:171-280 977:281-283 978:284-452] [-1, 982, 9

```
################################
## Counts of transcripts, etc.
################################
Total trinity 'genes':    81568
Total trinity transcripts:    148557
Percent GC: 39.50

########################################
Stats based on ALL transcript contigs:
########################################

    Contig N10: 5382
    Contig N20: 3754
    Contig N30: 2866
    Contig N40: 2251
    Contig N50: 1769

    Median contig length: 527
    Average contig: 1006.00
    Total assembled bases: 149448583


#####################################################
## Stats based on ONLY LONGEST ISOFORM per 'GENE':
#####################################################

    Contig N10: 5242
    Contig N20: 3620
    Contig N30: 2695
    Contig N40: 2062
    Contig N50: 1577

    Median contig length: 434
    Average contig: 872.76
    Total assembled bases: 71189166
```        

In [2]:
!fgrep -c ">" /Users/sr320/data-genomic/tentacle/trinity.kmer2.fa

148557


In [3]:
!cp /Users/sr320/data-genomic/tentacle/trinity.kmer2.fa \
/Users/sr320/data-genomic/tentacle/OlyO_v6_transcriptome.fa

## Running blastx

```
%%bash
for f in query.part*
do
blastx \
-query $f \
-db /usr/local/bioinformatics/dbs/uniprot_sprot.fasta \
-evalue 1e-5 \
-max_target_seqs 1 \
-max_hsps 1 \
-outfmt 6 \
-num_threads 16 \
-out blastout_"$f"_sp \
2> error-blastout_"$f"_sp
done
```

# Expression

Ran RNA-seq on all four samples as  below to version 6.

<img src="http://eagle.fish.washington.edu/cnidarian/skitch/sr320’s_iMac_1C0748FB.png" alt="sr320’s_iMac_1C0748FB.png"/>

Then "setup experiment"

In [1]:
!head data/Oly6_FvM-totalcounts.csv

In [ ]:
# Might thave to rename contigs?

Current naming format `TR1|c0_g1_i1`

```
The accession encodes the Trinity 'gene' and 'isoform' information. In the example above, the accession 'TRINITY_DN1000|c115_g5_i1' indicates Trinity read cluster 'TRINITY_DN1000|c115', gene 'g5', and isoform 'i1'. Because a given run of trinity involves many many clusters of reads, each of which are assembled separately, and because the 'gene' numberings are unique within a given processed read cluster, the 'gene' identifier should be considered an aggregate of the read cluster and corresponding gene identifier, which in this case would be 'TRINITY_DN1000|c115_g5'.

So, in summary, the above example corresponds to 'gene id: TRINITY_DN1000|c115_g5' encoding 'isoform id: TRINITY_DN1000|c115_g5_i1'.
```

In [5]:
!fgrep ">" /Volumes/Monarch/quarter-shell/OlyO_v6_transcriptome.fa | head -50



>TR1|c0_g1_i1 len=320 path=[639:0-301 640:302-319] [-1, 639, 640, -2]
>TR1|c0_g2_i1 len=323 path=[637:0-301 638:302-322] [-1, 637, 638, -2]
>TR2|c0_g1_i1 len=359 path=[834:0-181 838:182-235 837:236-358] [-1, 834, 838, 837, -2]
>TR3|c0_g1_i1 len=256 path=[234:0-255] [-1, 234, -2]
>TR4|c0_g1_i1 len=330 path=[706:0-106 707:107-130 709:131-223 705:224-329] [-1, 706, 707, 709, 705, -2]
>TR5|c0_g1_i1 len=226 path=[407:0-225] [-1, 407, -2]
>TR6|c0_g1_i1 len=400 path=[804:0-194 805:195-218 806:219-399] [-1, 804, 805, 806, -2]
>TR7|c0_g1_i1 len=311 path=[577:0-310] [-1, 577, -2]
>TR8|c0_g1_i1 len=378 path=[760:0-264 761:265-288 762:289-377] [-1, 760, 761, 762, -2]
>TR9|c0_g1_i1 len=256 path=[755:0-51 765:52-64 763:65-75 761:76-122 759:123-179 742:180-203 743:204-255] [-1, 755, 765, 763, 761, 759, 742, 743, -2]
>TR10|c0_g1_i1 len=240 path=[985:0-191 986:192-194 987:195-239] [-1, 985, 986, 987, -2]
>TR10|c0_g2_i1 len=453 path=[982:0-146 983:147-170 988:171-280 977:281-283 978:284-452] [-1, 982, 9

In [7]:
#Renaming for CLC

!sed 's/|c/_c/g' /Volumes/Monarch/quarter-shell/OlyO_v6_transcriptome.fa \
> /Volumes/Monarch/quarter-shell/OlyO_v6_transcriptome_rn.fa

In [8]:
!head /Volumes/Monarch/quarter-shell/OlyO_v6_transcriptome_rn.fa

>TR1_c0_g1_i1 len=320 path=[639:0-301 640:302-319] [-1, 639, 640, -2]
GACGAAAAACAAACACATAATCAATCAATCAATCAATCAATCAAATAACAGAGATTCAAT
CCATAGTAACAGTATACCTTACAGCGATATAACAGTCTGGTTATTCTATAAAATCTATAT
CTACATGTATTATTAACACACATTACTTATTATATAATGTTCTGGTTGCTTGAATTATGG
AAGTATAAAAACAATGTATAACCGGGACCATTATTTATACAGAGAAAAACTAGCAAAGTG
TTTGGTTTTAAAACTCGAATTGACTGACATTGACAGTGGCATATTTATAATTTTGTAGGA
TGTTAATCAACACATAACAT
>TR1_c0_g2_i1 len=323 path=[637:0-301 638:302-322] [-1, 637, 638, -2]
GACGAAAAACAAACACATAATCAATCAATCAATCAATCAATCAAATAACAGAGATTCAAT
CCATAGTAACAGTATACCTTACAGCGATATAACAGTCTGGTTATTCTATAAAATCTATAT


In [ ]:
reimporting